In [1]:
! pip install \
  cudf-cu12 \
  cupy-cuda12x \
  dask-cudf-cu12 \
  hvplot \
  holoviews \
  datashader \
  bokeh

Defaulting to user installation because normal site-packages is not writeable
Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.2/42.2 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.8/41.8 kB 14.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.6/2.6 MB 16.5 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 627.3/627.3 MB 21.5 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.4/21.4 MB 21.5 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 920.1/920.1 kB 20.8 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 20.2 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.5/3.5 MB 18.0 MB/s eta 0:00:00a 0:00:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 40.5/40.5 MB 22.9 MB/s eta 0:00:0000:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.6/89.6 MB 21.9 MB/s eta 0

In [9]:
import time
import pandas as pd
import numpy as np
import hvplot.pandas       # registers hvplot for pandas
import holoviews as hv
from bokeh.io import output_notebook, show

M = 100_000_000  # go smaller on CPU

t0 = time.perf_counter()
pdf = pd.DataFrame({
    "x": np.random.random(M) * 100.0,
    "y": np.random.random(M) * 100.0,
    "value": np.random.standard_normal(M),
})
t1 = time.perf_counter()
print(f"Created pandas DataFrame with {M:,} rows in {t1 - t0:.2f} seconds")

# %%time
scatter_cpu = pdf.hvplot.points(
    x="x",
    y="y",
    c="value",
    cmap="Viridis",
    width=800,
    height=600,
    datashade=True,      # still uses Datashader but on CPU arrays
    dynspread=True,
    colorbar=True,
    title="10M-point CPU scatterplot with Datashader"
)
show(hv.render(scatter_cpu))


Created pandas DataFrame with 100,000,000 rows in 6.74 seconds


You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/js_callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html



In [13]:
# %%time
scatter_cpu = pdf.hvplot.points(
    x="x",
    y="y",
    c="value",
    cmap="Viridis",
    width=800,
    height=600,
    datashade=True,      # still uses Datashader but on CPU arrays
    dynspread=True,
    colorbar=True,
    title="10M-point CPU scatterplot with Datashader"
)
show(hv.render(scatter_cpu))


You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/js_callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html



In [11]:
import time

import cupy as cp      # GPU ndarray library
import cudf            # GPU DataFrame library (RAPIDS)
import hvplot.cudf     # hvPlot extension for cuDF
import holoviews as hv
from bokeh.io import output_notebook, show

hv.extension("bokeh")
output_notebook()

# ----------------------------
# 1. Generate a HUGE dataset on the GPU
# ----------------------------

N = 100_000_000  # 100 million points – big enough to hurt on CPU

t0 = time.perf_counter()

gdf = cudf.DataFrame({
    "x": cp.random.random(N) * 100.0,           # uniform in [0, 100)
    "y": cp.random.random(N) * 100.0,
    "value": cp.random.standard_normal(N),      # something we can aggregate
    "category": cp.random.randint(0, 5, size=N) # 5 categories
})

t1 = time.perf_counter()
print(f"Created cuDF DataFrame with {N:,} rows in {t1 - t0:.2f} seconds")

# ----------------------------
# 2. Heavy visualization: 50M-point scatter via Datashader on GPU
# ----------------------------
# hvPlot + Datashader will:
#  - push the aggregation to Datashader
#  - operate on cuDF/CuPy on the GPU
#  - render a rasterized image to the browser

# You can try datashade=True OR rasterize=True.
# datashade=True performs dynamic aggregation; rasterize=True is similar
# but with a slightly different pipeline. Both are GPU-backed with cuDF.

# %%time
scatter_gpu = gdf.hvplot.points(
    x="x",
    y="y",
    c="value",              # color by "value"
    cmap="Viridis",
    width=800,
    height=600,
    datashade=True,         # key: Datashader aggregation (GPU with cuDF)
    dynspread=True,         # expand small dense regions for visibility
    colorbar=True,
    title="100M-point GPU scatterplot with RAPIDS + Datashader"
)

show(hv.render(scatter_gpu))


Loading BokehJS ...

Created cuDF DataFrame with 100,000,000 rows in 1.82 seconds


You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/js_callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html



In [12]:
scatter_gpu = gdf.hvplot.points(
    x="x",
    y="y",
    c="value",              # color by "value"
    cmap="Viridis",
    width=800,
    height=600,
    datashade=True,         # key: Datashader aggregation (GPU with cuDF)
    dynspread=True,         # expand small dense regions for visibility
    colorbar=True,
    title="100M-point GPU scatterplot with RAPIDS + Datashader"
)

show(hv.render(scatter_gpu))

You are generating standalone HTML/JS output, but trying to use real Python
callbacks (i.e. with on_change or on_event). This combination cannot work.

Only JavaScript callbacks may be used with standalone output. For more
information on JavaScript callbacks with Bokeh, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/interaction/js_callbacks.html

Alternatively, to use real Python callbacks, a Bokeh server application may
be used. For more information on building and running Bokeh applications, see:

    https://docs.bokeh.org/en/latest/docs/user_guide/server.html

